In [1]:
import numpy as np

In [2]:
class Neuron:
    def __init__(self, weights, bias, lr):
        self.weights = weights
        self.bias = bias
        self.error = float
        self.delta_weights = []
        self.delta_bias = 0
        self.lr = lr
    
    def calculate_neuron(self, inputs):
        """
        Calculate the output of this neuron
    
        """
        list_outputs = []
        if len(inputs) == len(self.weights):
            for x, weight in zip(inputs, self.weights):
                list_outputs.append(x*weight)
        else:
            raise ValueError("The list of inputs and weights must have the same length")
        
        self.sum_output = sum(list_outputs)
        outcome = self.sum_output + self.bias
        output_sigmoid = self.sigmoid_function(outcome)
        return output_sigmoid
    
    def sigmoid_function(self, x):
        return 1/(1+np.exp(-x))
    
    def set_delta(self):
        for weight in self.weights:
            self.delta_weights.append(weight*self.error) # delta weight is lr * output --> 
        self.delta_bias = self.lr * self.error
        
    def get_deltas(self):
        # Function that returns a deltas on index for calculating next (previous) layer error
        deltas = []
        for weight in self.weights:
            deltas.append(weight*self.error)
        return deltas
    
    def update_neuron(self):
        for index in range(len(self.weights)):
            self.weights[index] -= self.delta_weights[index]
        
        self.bias-= self.delta_bias
        
        self.delta_weights = []
    
class Output_neuron(Neuron):
    def calculate_error(self, output_neuron, target):
        self.error = output_neuron * (1 - output_neuron) * - (target - output_neuron)

    def gradient(self, output):
        return output * self.error    
        
    def calculate_delta(self, output_neural_network):
        for weight in self.weights:
            self.delta_weights.append(self.lr * self.gradient(output_neural_network))
        self.delta_bias = self.lr * self.error
        
class Hidden_neuron(Neuron):    
    def calculate_error(self, deltas_weight):
        self.error += sum([delta*weight for delta, weight in zip(deltas_weight, self.weights)])
        
    def calculate_delta(self):
        for weight in self.weights:
            self.delta_weights.append(self.error * weight)
        self.delta_bias = self.bias * self.error

In [3]:
class Neuron_layer:
    def __init__(self, neurons):
        self.neurons = neurons
    
    def calculate_layer(self, inputs):
        output = []
        for neuron in self.neurons:
            output.append(neuron.calculate_neuron(inputs))
        return output
    
    def set_output_layer(self, outputNN, target):
        for neuron in self.neurons:
            neuron.calculate_error(outputNN, target) # --> let op outputneuron functie wordt hier aangeroepen. -> check dit
            neuron.calculate_delta(outputNN)
    
    def set_hidden_layer(self, deltas_right_layer):
        for index in range(len(self.neurons)):
            self.neurons[index].calculate_error([deltas[index] for deltas in delta_right_layer])
    
    def get_deltas_layer(self):
        deltas_layer = []
        for neuron in self.neurons:
            delta_layer.append(neuron.get_deltas())
        return deltas_layer
        
    def update_layer(self):
        for neuron in self.neurons:
            neuron.update_neuron()
    
    def __str__(self):
        return f'The layer consist out of these neurons: {self.neurons}'

In [4]:
class Neuron_network:
    def __init__(self, neuron_layers):
        self.neuron_layers = neuron_layers
    
    def feed_forward(self, inputs):
        for neuron_layer in self.neuron_layers:
            inputs = neuron_layer.calculate_layer(inputs)
        return inputs
    
    def __str__(self):
        return f'The network consist out of these perceptron_layers: {self.neuron_layers}'
    
    def MSE(self, target_list, output_list): # loss function 
        return np.sum([(a-b)**2 for a,b in zip(target_list, output_list)])
    
    def train_nn(self, posible_inputs):
        """
        Put in like this [[[0, 0], 0],
                          [[0, 1], 0],
                          [[1, 0], 0],
                          [[1, 1], 1]]
        """
        print('x1 x2 target output')
        error = 1 # The error is unknown but will be assigned after the first check
        epoch = 0
        while error < -0.1 or error > 0.1: #epoch < 100: #
            li = []
            for posible_input in posible_inputs:  
                outputNN = self.feed_forward(posible_input[0])[0]
                li.append(outputNN)
            
                # sets delta of weights and bias of outputlayer
                print('________')
                print(outputNN, posible_input[1])
                print('__________')
            
                # backpropagation
                
                self.neuron_layers[-1].set_output_layer(outputNN, posible_input[1])
                
                for left_layer, right_layer in zip(self.neuron_layers[::-1], self.neuron_layers[-2::-1]): # Starting at -2 because last layer is output layer
                    deltas_next_layer = right_layer.get_deltas_layer()
                    
                    leftlayer.set_hidden_layer(deltas_next_layer)
                
                for layer in self.neuron_layers:
                    layer.update_layer()

            error = self.MSE([x[1] for x in posible_inputs], li)
            print('error = ', error)
            if error > -0.1 and error < 0.1:
                print('network trained!')
            
            epoch+=1

In [5]:
and_neuron = Output_neuron([1,1], 1, 0.1)

output_layer = Neuron_layer([and_neuron])

neural_network_AND = Neuron_network([output_layer])

In [6]:
neural_network_AND.train_nn([[[0, 0], 1],
                             [[0, 1], 0],
                             [[1, 0], 0],
                             [[1, 1], 0]])

x1 x2 target output
________
0.7310585786300049 1
__________
________
0.8817547745877533 0
__________
________
0.8799390894680806 0
__________
________
0.9508255425345699 0
__________
error =  2.528182984146887
________
0.7275747151508574 1
__________
________
0.8781506566845966 0
__________
________
0.8762496635250535 0
__________
________
0.9483513380453333 0
__________
error =  2.512547844860868
________
0.7239636847530552 1
__________
________
0.874354003456465 0
__________
________
0.8723627063479787 0
__________
________
0.9456919895323153 0
__________
error =  2.496041001187817
________
0.720219202853324 1
__________
________
0.8703518805969792 0
__________
________
0.8682650238359599 0
__________
________
0.9428305310425842 0
__________
error =  2.478603252393629
________
0.7163347229695894 1
__________
________
0.8661305092707366 0
__________
________
0.8639425830212794 0
__________
________
0.9397483519974104 0
__________
error =  2.460171800321654
________
0.712303452673676 

error =  0.7138126980540694
________
0.31218366986242424 1
__________
________
0.29206960338043453 0
__________
________
0.2904588840549438 0
__________
________
0.26608518847644014 0
__________
error =  0.7135636480757128
________
0.31165736544354655 1
__________
________
0.29150390716244157 0
__________
________
0.28990066871711834 0
__________
________
0.2655097577820656 0
__________
error =  0.7133279396392119
________
0.31114289067270107 1
__________
________
0.2909532858885214 0
__________
________
0.2893573151275689 0
__________
________
0.2649516668085364 0
__________
error =  0.7131049732025468
________
0.3106398795616244 1
__________
________
0.2904172457143499 0
__________
________
0.28882833701439886 0
__________
________
0.2644103251649487 0
__________
error =  0.7128941805754578
________
0.3101479796663983 1
__________
________
0.28989531211622616 0
__________
________
0.2883132671033005 0
__________
________
0.26388516647914423 0
__________
error =  0.712695023020821
___

________
0.24703357057429082 0
__________
error =  0.7138054066667043
________
0.28711175185219046 1
__________
________
0.2696051523214175 0
__________
________
0.26827991674023133 0
__________
________
0.24700394446229446 0
__________
error =  0.7138816548115855
________
0.2869933985633997 1
__________
________
0.26953206141622416 0
__________
________
0.2682077142064787 0
__________
________
0.24697526118142063 0
__________
error =  0.7139581034189455
________
0.2868759710130926 1
__________
________
0.269459911142729 0
__________
________
0.2681364406037948 0
__________
________
0.24694749641401514 0
__________
error =  0.7140347411963894
________
0.28675945157947547 1
__________
________
0.2693886801709648 0
__________
________
0.26806607487158673 0
__________
________
0.24692062646977975 0
__________
error =  0.7141115571887526
________
0.28664382307342195 1
__________
________
0.26931834771137075 0
__________
________
0.26799659648267105 0
__________
________
0.24689462826870337

________
0.2646159102794245 0
__________
________
0.2633506838487816 0
__________
________
0.24643198046060677 0
__________
error =  0.722039978992138
________
0.27747872470238594 1
__________
________
0.2645837089252412 0
__________
________
0.2633188656065065 0
__________
________
0.2464360498327528 0
__________
error =  0.7221090839277957
________
0.2774091232112032 1
__________
________
0.2645516360182189 0
__________
________
0.26328717422929887 0
__________
________
0.2464401577268031 0
__________
error =  0.7221780307923789
________
0.2773397454270435 1
__________
________
0.2645196899481391 0
__________
________
0.2632556081267296 0
__________
________
0.2464443026175391 0
__________
error =  0.7222468194125293
________
0.27727058971217255 1
__________
________
0.26448786913996564 0
__________
________
0.2632241657431205 0
__________
________
0.2464484830187159 0
__________
error =  0.7223154496305785
________
0.2772016544576616 1
__________
________
0.26445617205300653 0
_____

__________
error =  0.7284472044475816
________
0.27117777285528455 1
__________
________
0.26172202765994307 0
__________
________
0.2604910134123138 0
__________
________
0.24691005780707329 0
__________
error =  0.7285004032574818
________
0.27112603808237434 1
__________
________
0.2616985432604788 0
__________
________
0.2604678048446725 0
__________
________
0.2469141714105459 0
__________
error =  0.7285534653101119
________
0.27107443834570855 1
__________
________
0.26167511657714115 0
__________
________
0.26044465328616667 0
__________
________
0.24691827078640852 0
__________
error =  0.7286063909421865
________
0.27102297319533175 1
__________
________
0.2616517473782308 0
__________
________
0.2604215585080296 0
__________
________
0.2469223558929916 0
__________
error =  0.7286591804905518
________
0.27097164218455155 1
__________
________
0.2616284354350286 0
__________
________
0.26039852028443816 0
__________
________
0.24692642669136072 0
__________
error =  0.728711

...

0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
____

0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
___

________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579

________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.2516085238761509 0
__________
________
0.25049355758579017 0
__________
________
0.24790270988157578 0
__________
error =  0.7499831453890277
________
0.25001765344557764 1
__________
________
0.25160852387615

KeyboardInterrupt: 

In [ ]:
inputs = [[0,0],[0,1],[1,0],[1,1]]

print('x1, x2, carry, sum')
for input_x in inputs:
    print(input_x, '   ', neural_network_AND.feed_forward(input_x))